In [22]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.decomposition import PCA
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
from sklearn.manifold import TSNE

In [23]:
df = pd.read_csv('./train.csv')

Log_Number  \
0               0   
1               1   
2               2   
3               3   
4               4   
...           ...   
44995       44995   
44996       44996   
44997       44997   
44998       44998   
44999       44999   

                                                                                                   payload  \
0      GET /forum1_professionnel.asp?n=/.\\\"./.\\\"./.\\\"./.\\\"./.\\\"./boot.ini&amp;nn=100&amp;page...   
1      POST /owa/auth/logon.aspx?replaceCurrent=1%22%29%20AND%209294%3DUTL_INADDR.GET_HOST_ADDRESS%28CH...   
2      GET /goods/goods_search?display_type=list&arr_search_list%5B0%5D%5Bsearch_type%5D=-1839%20or%201...   
3                                                                                   GET / HTTP/1.1\r\n\r\n   
4      GET /sub_04_1_read.php?page=1&id=31%29%3BSELECT%20%2A%20FROM%20GENERATE_SERIES%289156%2C9156%2CC...   
...                                                                                                    ...   
44995  GET /app/javascript/js/skin-responsive.js?v=%3B HTTP/1.1\r\nHost: www.mall.shop\r\nUser-Agent: M...   
44996  GET /board/?category=type+%25SYSTEMROOT%25%5Cwin.ini&goods_seq=&id=goods_qna&iframe=&page=&perpa...   
44997  POST /sub_02_4.php HTTP/1.1\r\nContent-Length: 118\r\nCache-Control: no-cache\r\nCookie: df8k365...   
44998  GET /admin/myadmin HTTP/1.1\r\nHost: lab.college.school\r\nUser-Agent: Mozilla/4.0 (compatible; ...   
44999  GET /goods/goods_search?display_type=list&arr_search_list%5B0%5D%5Bsearch_type%5D=Gm.name&arr_se...   

               label_action  
0      System_Cmd_Execution  
1      System_Cmd_Execution  
2             SQL_Injection  
3                 HOST_Scan  
4      System_Cmd_Execution  
...                     ...  
44995  System_Cmd_Execution  
44996  System_Cmd_Execution  
44997         SQL_Injection  
44998       Path_Disclosure  
44999    Vulnerability_Scan  

[45000 rows x 3 columns]

In [24]:
label_ = list(set(df['label_action']))
label_cnt = len(label_)

idx = []
for i in range (0, label_cnt):
    idx.append(i)
ldf = df.replace(label_, idx)

Log_Number  \
0               0   
1               1   
2               2   
3               3   
4               4   
...           ...   
44995       44995   
44996       44996   
44997       44997   
44998       44998   
44999       44999   

                                                                                                   payload  \
0      GET /forum1_professionnel.asp?n=/.\\\"./.\\\"./.\\\"./.\\\"./.\\\"./boot.ini&amp;nn=100&amp;page...   
1      POST /owa/auth/logon.aspx?replaceCurrent=1%22%29%20AND%209294%3DUTL_INADDR.GET_HOST_ADDRESS%28CH...   
2      GET /goods/goods_search?display_type=list&arr_search_list%5B0%5D%5Bsearch_type%5D=-1839%20or%201...   
3                                                                                   GET / HTTP/1.1\r\n\r\n   
4      GET /sub_04_1_read.php?page=1&id=31%29%3BSELECT%20%2A%20FROM%20GENERATE_SERIES%289156%2C9156%2CC...   
...                                                                                                    ...   
44995  GET /app/javascript/js/skin-responsive.js?v=%3B HTTP/1.1\r\nHost: www.mall.shop\r\nUser-Agent: M...   
44996  GET /board/?category=type+%25SYSTEMROOT%25%5Cwin.ini&goods_seq=&id=goods_qna&iframe=&page=&perpa...   
44997  POST /sub_02_4.php HTTP/1.1\r\nContent-Length: 118\r\nCache-Control: no-cache\r\nCookie: df8k365...   
44998  GET /admin/myadmin HTTP/1.1\r\nHost: lab.college.school\r\nUser-Agent: Mozilla/4.0 (compatible; ...   
44999  GET /goods/goods_search?display_type=list&arr_search_list%5B0%5D%5Bsearch_type%5D=Gm.name&arr_se...   

       label_action  
0                 8  
1                 8  
2                 4  
3                 1  
4                 8  
...             ...  
44995             8  
44996             8  
44997             4  
44998             3  
44999             0  

[45000 rows x 3 columns]

# 0. Preprocessing

## 0.1. Decode URL
URL은 %NN 형태로 인코딩되어있기 때문에 디코딩을 해줄 것이다.

In [25]:
from urllib.parse import unquote
#test
test_url = ldf.payload[4]
dec_url = unquote(test_url)
print("Before:", test_url)
print("After:", dec_url)



Before: GET /sub_04_1_read.php?page=1&id=31%29%3BSELECT%20%2A%20FROM%20GENERATE_SERIES%289156%2C9156%2CCASE%20WHEN%20%289156%3D5350%29%20THEN%201%20ELSE%200%20END%29%20LIMIT%201-- HTTP/1.1\r\nCache-Control: no-cache\r\nUser-Agent: sqlmap/1.6.10#stable (https://sqlmap.org)\r\nReferer: http://10.0.17.20:80/sub_04_1_read.php\r\nHost: 10.0.17.20\r\nAccept: */*\r\nAccept-Encoding: gzip,deflate\r\nConnection: close\r\n\r\n
After: GET /sub_04_1_read.php?page=1&id=31);SELECT * FROM GENERATE_SERIES(9156,9156,CASE WHEN (9156=5350) THEN 1 ELSE 0 END) LIMIT 1-- HTTP/1.1\r\nCache-Control: no-cache\r\nUser-Agent: sqlmap/1.6.10#stable (https://sqlmap.org)\r\nReferer: http://10.0.17.20:80/sub_04_1_read.php\r\nHost: 10.0.17.20\r\nAccept: */*\r\nAccept-Encoding: gzip,deflate\r\nConnection: close\r\n\r\n


이런 형태로 모든 스트링에 적용시켜준다

In [26]:
from urllib.parse import unquote
decoded_payload = []
for url in ldf.payload:
    decoded_payload.append(unquote(url))
pd.options.display.max_colwidth = 100
ldf.payload = decoded_payload


0        GET /forum1_professionnel.asp?n=/.\\\"./.\\\"./.\\\"./.\\\"./.\\\"./boot.ini&amp;nn=100&amp;page...
1        POST /owa/auth/logon.aspx?replaceCurrent=1") AND 9294=UTL_INADDR.GET_HOST_ADDRESS(CHR(113)||CHR(...
2        GET /goods/goods_search?display_type=list&arr_search_list[0][search_type]=-1839 or 1=2&arr_searc...
3                                                                                     GET / HTTP/1.1\r\n\r\n
4        GET /sub_04_1_read.php?page=1&id=31);SELECT * FROM GENERATE_SERIES(9156,9156,CASE WHEN (9156=535...
                                                        ...                                                 
44995    GET /app/javascript/js/skin-responsive.js?v=; HTTP/1.1\r\nHost: www.mall.shop\r\nUser-Agent: Moz...
44996    GET /board/?category=type+%SYSTEMROOT%\win.ini&goods_seq=&id=goods_qna&iframe=&page=&perpage=&po...
44997    POST /sub_02_4.php HTTP/1.1\r\nContent-Length: 118\r\nCache-Control: no-cache\r\nCookie: df8k365...
44998    GET /admin

In [27]:
ldf.to_csv("./decoded.csv", escapechar='\\')

잘 디코딩이 된 것을 확인할 수 있다.

## 0.2. 불필요한 데이터 제거
payload의 모든 내용이 학습에 도움이 되는 것은 아니다. 
문자열을 feature data로 사용할 때 중요한 것은 실제로 공격에 사용된 부분이다. 
따라서 크게 영향을 주지 않을 것으로 부분들을 제거할것이다

In [28]:
duplicate_values = ldf['payload'].duplicated()
i = 0
cnt = 0
for pl in df.payload:
    if (duplicate_values[i] == True):
        cnt += 1
    i += 1
print("Number of dupes: ", cnt)

GET / HTTP/1.1\r\n\r\n
GET /admin/login.php HTTP/1.0\r\nHost: 10.0.17.19\r\nUser-Agent: Mozilla/5.0 (Hydra)\r\n\r\n
GET /admin/login.php HTTP/1.0\r\nHost: 10.0.17.19\r\nUser-Agent: Mozilla/5.0 (Hydra)\r\n\r\n
GET /admin/login.php HTTP/1.0\r\nHost: 10.0.17.19\r\nUser-Agent: Mozilla/5.0 (Hydra)\r\n\r\n
GET / HTTP/1.1\r\n\r\n
GET /admin/login.php HTTP/1.0\r\nHost: 10.0.17.19\r\nUser-Agent: Mozilla/5.0 (Hydra)\r\n\r\n
GET / HTTP/1.1\r\n\r\n
GET /member/login HTTP/1.0\r\nHost: 10.0.17.19\r\nUser-Agent: Mozilla/5.0 (Hydra)\r\n\r\n
POST /controller/login.php HTTP/1.1\r\nContent-Length: 240\r\nCache-Control: no-cache\r\nUser-Agent: sqlmap/1.6.7#stable (https://sqlmap.org)\r\nCookie: PHPSESSID=8ndjmp9vjimv0n3ppkhi1mh9ln\r\nHost: 10.0.17.20\r\nAccept: */*\r\nAccept-Encoding: gzip,deflate\r\nContent-Type: application/x-www-form-urlencoded; charset=utf-8\r\nConnection: close\r\n\r\n
GET / HTTP/1.1\r\n\r\n
GET /member/login HTTP/1.0\r\nHost: 10.0.17.19\r\nUser-Agent: Mozilla/5.0 (Hydra)\r\n\r\n
GET

In [29]:
ldf = ldf.drop_duplicates(subset=['payload'])

Log_Number  \
0               0   
1               1   
2               2   
3               3   
4               4   
...           ...   
44993       44993   
44995       44995   
44996       44996   
44997       44997   
44998       44998   

                                                                                                   payload  \
0      GET /forum1_professionnel.asp?n=/.\\\"./.\\\"./.\\\"./.\\\"./.\\\"./boot.ini&amp;nn=100&amp;page...   
1      POST /owa/auth/logon.aspx?replaceCurrent=1") AND 9294=UTL_INADDR.GET_HOST_ADDRESS(CHR(113)||CHR(...   
2      GET /goods/goods_search?display_type=list&arr_search_list[0][search_type]=-1839 or 1=2&arr_searc...   
3                                                                                   GET / HTTP/1.1\r\n\r\n   
4      GET /sub_04_1_read.php?page=1&id=31);SELECT * FROM GENERATE_SERIES(9156,9156,CASE WHEN (9156=535...   
...                                                                                                    ...   
44993  GET /admin/captcha/securimage_show?160c3e6d29ea99621a9ddced77261577=../../../../../../../../../....   
44995  GET /app/javascript/js/skin-responsive.js?v=; HTTP/1.1\r\nHost: www.mall.shop\r\nUser-Agent: Moz...   
44996  GET /board/?category=type+%SYSTEMROOT%\win.ini&goods_seq=&id=goods_qna&iframe=&page=&perpage=&po...   
44997  POST /sub_02_4.php HTTP/1.1\r\nContent-Length: 118\r\nCache-Control: no-cache\r\nCookie: df8k365...   
44998  GET /admin/myadmin HTTP/1.1\r\nHost: lab.college.school\r\nUser-Agent: Mozilla/4.0 (compatible; ...   

       label_action  
0                 8  
1                 8  
2                 4  
3                 1  
4                 8  
...             ...  
44993             3  
44995             8  
44996             8  
44997             4  
44998             3  

[31754 rows x 3 columns]

## Tokenizing
공백, &, =, :, ;

In [30]:
import re


split_payload = []
for url in ldf.payload:
    split_payload.append(re.split('?|;|,|:| |&|=',url))
pd.options.display.max_colwidth = 100
ldf.payload = split_payload

error: nothing to repeat at position 0

In [ ]:
ldf.to_csv("./split.csv", escapechar='\\')